In [68]:
import numpy as np
import pandas as pd
from flask import Flask,request
from flask_cors import CORS
from flask import jsonify
from flask_restful import reqparse

In [66]:
AML_table=pd.read_csv('../txn_records_0411.csv')
AML_accts=pd.read_csv("../all_accts_list.csv", encoding='big5')

In [86]:
def Table_filter(acct_nbr, T1, T2):
    output_L1=AML_table[AML_table['acct_nbr']==acct_nbr] # L1 transactions
    output_L1['level']='L1'
    Target_acct=AML_table[AML_table['acct_nbr']==acct_nbr]['txn_acct'].unique().tolist() # get L1 transactions account numbers
    output_L2=AML_table[AML_table['acct_nbr'].isin(Target_acct)]# L2 transactions
    output_L2['level']='L2'
    links = pd.concat([output_L1, output_L2])
    links = links[(links['indegree_amt']>=T) | (links['outdegree_amt']>=T)]
    links = links.drop_duplicates()
    output_links = links.to_json(orient="records", force_ascii=False)
    '''
       get all nodes and required informations
    '''    
    accts = links['acct_nbr'].unique().tolist()
    txn_accts = links['txn_acct'].unique().tolist()
    for i in txn_accts:
        if i not in accts:
            accts.append(i)
    nodes = AML_accts[AML_accts['acct_nbr'].isin(accts)]
    nodes = nodes.drop_duplicates()
    output_nodes = nodes.to_json(orient='records', force_ascii=False)
    
    final_answers = {
        "txn_records": output_links,
        "acct_list": output_nodes
    }
    
    return final_answers

In [87]:
Output=Table_filter("0000077BBD373A737851B5C6", 100000)

/Library/Frameworks/Python.framework/Versions/3.7/lib/python3.7/site-packages/ipykernel_launcher.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  This is separate from the ipykernel package so we can avoid doing imports until
/Library/Frameworks/Python.framework/Versions/3.7/lib/python3.7/site-packages/ipykernel_launcher.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  


In [88]:
Output

{'txn_records': '[{"customer_id":"F1695CEBB36BF2E36C","acct_nbr":"0000077BBD373A737851B5C6","txn_acct":"00000003F1BEB2C82CF6D770","txn_amt_ttl":14238372.0,"txn_cnt_ttl":25.0,"source_id":"00000003F1BEB2C82CF6D770","target_id":"0000077BBD373A737851B5C6","indegree_cnt":11.0,"indegree_amt":8308372.0,"outdegree_cnt":0.0,"outdegree_amt":0.0,"bank_code":"本行","alert":"T","level":"L1"},{"customer_id":"F1695CEBB36BF2E36C","acct_nbr":"0000077BBD373A737851B5C6","txn_acct":"0000077FDA595387F5967952","txn_amt_ttl":9100000.0,"txn_cnt_ttl":4.0,"source_id":"0000077FDA595387F5967952","target_id":"0000077BBD373A737851B5C6","indegree_cnt":1.0,"indegree_amt":2200000.0,"outdegree_cnt":0.0,"outdegree_amt":0.0,"bank_code":"本行","alert":"T","level":"L1"},{"customer_id":"F1695CEBB36BF2E36C","acct_nbr":"0000077BBD373A737851B5C6","txn_acct":"0000119102572F4DA8F5BB29","txn_amt_ttl":4600000.0,"txn_cnt_ttl":1.0,"source_id":"0000119102572F4DA8F5BB29","target_id":"0000077BBD373A737851B5C6","indegree_cnt":1.0,"indegree_